In [18]:
import torch
import torchvision.transforms.functional as TF
from torch.utils.data import Dataset, DataLoader
import json
import os
from PIL import Image, ImageDraw

class MaskDataset(Dataset):
    def __init__(self, json_files, image_size):
        self.json_files = json_files
        self.image_size = image_size

    def __len__(self):
        return len(self.json_files)

    def __getitem__(self, idx):
        json_path = self.json_files[idx]
        with open(json_path, 'r') as file:
            data = json.load(file)

        width, height = self.image_size
        mask_img = Image.new('L', (width, height), 0)
        draw = ImageDraw.Draw(mask_img)
        # 모든 shape에 대해 마스킹 적용
        for shape in data['shapes']:
            polygon = [coord for point in shape['points'] for coord in point]
            draw.polygon(polygon, outline=1, fill=255)
        
        mask_tensor = TF.to_tensor(mask_img)
        return mask_tensor, os.path.basename(json_path).split('.')[0]

if __name__ == "__main__":
    root_directory = '/home/hdd3/lee_hw/Hadoop_data/2.Validation/라벨링데이터'
    exclude_dirs = {"IR", "Lidar_Center", "Lidar_Left", "Lidar_Right"}
    json_files = []
    for dirpath, dirnames, filenames in os.walk(root_directory):
        dirnames[:] = [d for d in dirnames if d not in exclude_dirs]
        for filename in filenames:
            if filename.endswith('.json'):
                json_files.append(os.path.join(dirpath, filename))

    dataset = MaskDataset(json_files=json_files, image_size=(1920, 1080))
    reserved_cores = 2
    available_cores = max(1, os.cpu_count() - reserved_cores)
    
    # DataLoader with multiprocessing
    loader = DataLoader(dataset, batch_size=1, shuffle=True, num_workers=available_cores)

    output_dir = '/home/hdd3/lee_hw/Hadoop_project/test_data_set'

    for tensor, base_filename in loader:
        # Ensure base_filename is a string and not a tuple
        base_filename = base_filename[0] if isinstance(base_filename, tuple) else base_filename
        output_path = os.path.join(output_dir, f"{base_filename}_mask.png")
        TF.to_pil_image(tensor.squeeze(0)).save(output_path)
        print(f"Mask image saved to {output_path}")



Mask image saved to /home/hdd3/lee_hw/Hadoop_project/Right_data/masking_data/85CR_SD_20220117_051746_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/Right_data/masking_data/85CR_SD_20220117_051099_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/Right_data/masking_data/85CR_SD_20220119_054592_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/Right_data/masking_data/85CR_SD_20220117_050006_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/Right_data/masking_data/85CR_SD_20220117_050087_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/Right_data/masking_data/85CR_SD_20220119_056880_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/Right_data/masking_data/85CR_SD_20220117_049416_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/Right_data/masking_data/85CR_SD_20220119_053129_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/Right_data/masking_data/85CR_SD_20220117_051315_mask.png
Mask image

In [38]:
import torch
import torchvision.transforms.functional as TF
from torch.utils.data import Dataset, DataLoader
import json
import os
from PIL import Image, ImageDraw

class MaskDataset(Dataset):
    def __init__(self, json_files, image_size):
        self.json_files = json_files
        self.image_size = image_size

    def __len__(self):
        return len(self.json_files)

    def __getitem__(self, idx):
        json_path = self.json_files[idx]
        with open(json_path, 'r') as file:
            data = json.load(file)

        width, height = self.image_size
        mask_img = Image.new('L', (width, height), 0)
        draw = ImageDraw.Draw(mask_img)

        # 특정 객체만 마스킹 적용
        target_objects = {'car', 'truck', 'bicycle', 'bollard', 'bus', 'kickboard', 'labacon', 'motorcycle', 'pedestrian'}
        for shape in data['shapes']:
            if shape['label'] in target_objects:
                polygon = [coord for point in shape['points'] for coord in point]
                draw.polygon(polygon, outline=1, fill=255)
            
        mask_tensor = TF.to_tensor(mask_img)
        return mask_tensor, os.path.basename(json_path).split('.')[0]


if __name__ == "__main__":
    root_directory = '/home/hdd3/lee_hw/Hadoop_data/2.Validation/라벨링데이터'
    exclude_dirs = {"IR", "Lidar_Center", "Lidar_Left", "Lidar_Right"}
    json_files = []
    for dirpath, dirnames, filenames in os.walk(root_directory):
        dirnames[:] = [d for d in dirnames if d not in exclude_dirs]
        for filename in filenames:
            if filename.endswith('.json'):
                json_files.append(os.path.join(dirpath, filename))

    dataset = MaskDataset(json_files=json_files, image_size=(1920, 1080))
    reserved_cores = 2
    available_cores = max(1, os.cpu_count() - reserved_cores)
    
    # DataLoader with multiprocessing
    loader = DataLoader(dataset, batch_size=1, shuffle=True, num_workers=available_cores)

    output_dir = '/home/hdd3/lee_hw/Hadoop_project/test_data_set'

    for tensor, base_filename in loader:
        # Ensure base_filename is a string and not a tuple
        base_filename = base_filename[0] if isinstance(base_filename, tuple) else base_filename
        output_path = os.path.join(output_dir, f"{base_filename}_mask.png")
        TF.to_pil_image(tensor.squeeze(0)).save(output_path)
        print(f"Mask image saved to {output_path}")



Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CF_ND_20210916_017351_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CF_RD_20211130_068758_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CL_ND_20210722_000942_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CF_SD_20220119_052295_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CF_ND_20210728_005380_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CB_NN_20220204_061280_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CL_ND_20210722_002730_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CF_RD_20211130_065405_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CB_RN_20220214_075198_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CB_NN_20210915_015024_mask.png


In [37]:
import torch
import torchvision.transforms.functional as TF
from torch.utils.data import Dataset, DataLoader
import json
import os
from PIL import Image, ImageDraw

class MaskDataset(Dataset):
    def __init__(self, json_files, image_size):
        self.json_files = json_files
        self.image_size = image_size

    def __len__(self):
        return len(self.json_files)

    def __getitem__(self, idx):
        json_path = self.json_files[idx]
        with open(json_path, 'r') as file:
            data = json.load(file)

        width, height = self.image_size
        mask_img = Image.new('L', (width, height), 0)
        draw = ImageDraw.Draw(mask_img)
        # 모든 shape에 대해 마스킹 적용
        for shape in data['shapes']:
            polygon = [coord for point in shape['points'] for coord in point]
            draw.polygon(polygon, outline=1, fill=255)
        
        mask_tensor = TF.to_tensor(mask_img)
        return mask_tensor, os.path.basename(json_path).split('.')[0]

if __name__ == "__main__":
    root_directory = '/home/hdd3/lee_hw/Hadoop_data/2.Validation/라벨링데이터'
    exclude_dirs = {"IR", "Lidar_Center", "Lidar_Left", "Lidar_Right"}
    json_files = []
    for dirpath, dirnames, filenames in os.walk(root_directory):
        dirnames[:] = [d for d in dirnames if d not in exclude_dirs]
        for filename in filenames:
            if filename.endswith('.json'):
                json_files.append(os.path.join(dirpath, filename))

    dataset = MaskDataset(json_files=json_files, image_size=(1920, 1080))
    
    # DataLoader without multiprocessing
    loader = DataLoader(dataset, batch_size=1, shuffle=True, num_workers=0)

    output_dir = '/home/hdd3/lee_hw/Hadoop_project/test_data_set'

    for tensor, base_filename in loader:
        # Ensure base_filename is a string and not a tuple
        base_filename = base_filename[0] if isinstance(base_filename, tuple) else base_filename
        output_path = os.path.join(output_dir, f"{base_filename}_mask.png")
        TF.to_pil_image(tensor.squeeze(0)).save(output_path)
        print(f"Mask image saved to {output_path}")


Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CB_SD_20220119_052692_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CF_RD_20211229_045132_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CF_RD_20211229_045756_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CL_SD_20220119_055983_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CB_NN_20210915_014442_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CB_RD_20211229_047823_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CF_RD_20211130_063916_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CF_HD_20211216_037793_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CR_ND_20210923_027867_mask.png
Mask image saved to /home/hdd3/lee_hw/Hadoop_project/test_data_set/85CB_ND_20210923_027867_mask.png
